Scrape https://patents.google.com/ for images from specific publication numbers

In [1]:
import requests
from bs4 import BeautifulSoup as BS
import os
import time
import pandas as pd
import json
import re

In [2]:
SLEEP_IMAGES = 0.5 # seconds to pause between images
SLEEP_PATENT = 1 # seconds to pause between patents

In [3]:
# test variables

# URL = "https://realpython.github.io/fake-jobs/"
# URL = "https://patents.google.com/patent/EP3619893B1"
# identifier = "EP3619893B1"
# URL = "https://patents.google.com/patent/US2021323767A1"
# URL = "https://patents.google.com/patent/EP3895010A1"
# URL = "https://patents.google.com/patent/US20210309346A1"
# identifier = "US-2021309346-A1"
URL = "https://patents.google.com/patent/WO2021180039A1"
identifier = "WO-2021180039-A1"

In [4]:
json_input = "json_data/keyword_search_data_20211126.json"
# json_input = "json_data/assignee_search_data_20211203.json"

In [5]:
base_url = "https://patents.google.com/patent/"
root_folder = "image_downloads"
current_download = None

print("running patent scraper")
print("*" * 20)


json_inputs = ["json_data/assignee_search_data_20211203.json",
               "json_data/keyword_search_data_20211126.json"                ]

try:
    for json_input in json_inputs:

        print(f'--- loading input: {json_input} ---')

        all_data = []
        for line in open(json_input, 'r'):
            all_data.append(json.loads(line))
        df = pd.DataFrame(all_data)
        pubs = df["publication_number"]

        total_pubs = len(pubs)

        for i, pub in enumerate(pubs[:]):
            print(f'i: {i} / {total_pubs} --- publication_number: {pub}')
            identifier = pub
            text = pub
            # clean up some of the specific publication_number formats
            text = re.sub(r'(US-2021)', r'\g<1>0', text)
            text = re.sub(r'(US-2005)', r'\g<1>0', text)
            text = re.sub(r'(US-D\d\d\d\d\d\d-S)', r'\g<1>1', text)

            # remove dashes for the URL
            formatted = text.replace("-", "")
            URL = base_url + formatted
            print(f'URL: {URL}')

            target_folder = os.path.join(root_folder, identifier)
            #     print(f'target_folder {target_folder}')

            if not os.path.exists(target_folder):
                print(f'making directory {target_folder}')
                os.mkdir(target_folder)

                page = requests.get(URL)
            #     print(page.text)
                soup = BS(page.content, "html.parser")

                # get all image URLs
                results = soup.find_all(itemprop="full")
                print(f'found {len(results)} images')
            #     for result in results:
            #         print(result['content'])

                pdf_results = soup.find_all(itemprop="pdfLink")
                print(f'found {len(pdf_results)} PDFs')

                # get all images    
                for result in results:
                    img_url = result['content']
                    img_name = os.path.basename(img_url)
        #             print(img_name)
                    save_file_path = os.path.join(target_folder, img_name)
        #             print(save_file_path)

                    if not os.path.exists(save_file_path):
                        print(f'downloading {img_name} to {save_file_path}')
                        img_data = requests.get(img_url).content
                        with open(save_file_path, 'wb') as handler:
                            handler.write(img_data)
                        time.sleep(SLEEP_IMAGES)
                    else:
                        print(f'file {save_file_path} already exists')

                # get PDF
                for pdf_result in pdf_results:
                    pdf_url = pdf_result['href']
                    print(pdf_url)
            #         print(pdf_result)
                    pdf_name = pdf_result['href'].rsplit("/", 1)[1]
            #         print(pdf_name)
                    pdf_save_file_path = os.path.join(target_folder, pdf_name)
            #         print(pdf_save_file_path)

                    if not os.path.exists(pdf_save_file_path):
                        print(f'downloading {pdf_name} to {pdf_save_file_path}')
                        pdf_data = requests.get(pdf_url).content
                        with open(pdf_save_file_path, 'wb') as handler:
                            handler.write(pdf_data)
                        time.sleep(SLEEP_IMAGES)
                    else:
                        print(f'PDF {pdf_save_file_path} already exists')

                # pause before next patent
                time.sleep(SLEEP_PATENT)

            else:
                print(f'folder {target_folder} already exists, continuing to next publication_number')

            print("*" * 20)

    print("scraping complete")
except OSError as e:
    print ("Error: %s - %s." % (e.filename, e.strerror))
finally:
    if current_download:
        

running patent scraper
********************
--- loading input: json_data/assignee_search_data_20211203.json ---
i: 0 / 37660 --- publication_number: EP-3619893-B8
URL: https://patents.google.com/patent/EP3619893B8
folder image_downloads/EP-3619893-B8 already exists, continuing to next publication_number
********************
i: 1 / 37660 --- publication_number: EP-3786085-A4
URL: https://patents.google.com/patent/EP3786085A4
folder image_downloads/EP-3786085-A4 already exists, continuing to next publication_number
********************
i: 2 / 37660 --- publication_number: EP-3899827-A1
URL: https://patents.google.com/patent/EP3899827A1
folder image_downloads/EP-3899827-A1 already exists, continuing to next publication_number
********************
i: 3 / 37660 --- publication_number: US-2021323767-A1
URL: https://patents.google.com/patent/US20210323767A1
folder image_downloads/US-2021323767-A1 already exists, continuing to next publication_number
********************
i: 4 / 37660 --- publi

folder image_downloads/WO-2021154462-A1 already exists, continuing to next publication_number
********************
i: 707 / 37660 --- publication_number: AU-2018373029-B2
URL: https://patents.google.com/patent/AU2018373029B2
folder image_downloads/AU-2018373029-B2 already exists, continuing to next publication_number
********************
i: 708 / 37660 --- publication_number: AU-2020202180-B2
URL: https://patents.google.com/patent/AU2020202180B2
folder image_downloads/AU-2020202180-B2 already exists, continuing to next publication_number
********************
i: 709 / 37660 --- publication_number: EP-3857912-A1
URL: https://patents.google.com/patent/EP3857912A1
folder image_downloads/EP-3857912-A1 already exists, continuing to next publication_number
********************
i: 710 / 37660 --- publication_number: EP-3500510-B1
URL: https://patents.google.com/patent/EP3500510B1
folder image_downloads/EP-3500510-B1 already exists, continuing to next publication_number
********************
i: 

folder image_downloads/EP-3814895-A1 already exists, continuing to next publication_number
********************
i: 1484 / 37660 --- publication_number: EP-3814962-A1
URL: https://patents.google.com/patent/EP3814962A1
folder image_downloads/EP-3814962-A1 already exists, continuing to next publication_number
********************
i: 1485 / 37660 --- publication_number: EP-3689481-A4
URL: https://patents.google.com/patent/EP3689481A4
folder image_downloads/EP-3689481-A4 already exists, continuing to next publication_number
********************
i: 1486 / 37660 --- publication_number: US-10996640-B1
URL: https://patents.google.com/patent/US10996640B1
folder image_downloads/US-10996640-B1 already exists, continuing to next publication_number
********************
i: 1487 / 37660 --- publication_number: US-10999184-B2
URL: https://patents.google.com/patent/US10999184B2
folder image_downloads/US-10999184-B2 already exists, continuing to next publication_number
********************
i: 1488 / 3766

folder image_downloads/US-10922423-B1 already exists, continuing to next publication_number
********************
i: 2332 / 37660 --- publication_number: US-10922732-B1
URL: https://patents.google.com/patent/US10922732B1
folder image_downloads/US-10922732-B1 already exists, continuing to next publication_number
********************
i: 2333 / 37660 --- publication_number: US-10924286-B2
URL: https://patents.google.com/patent/US10924286B2
folder image_downloads/US-10924286-B2 already exists, continuing to next publication_number
********************
i: 2334 / 37660 --- publication_number: US-10925167-B2
URL: https://patents.google.com/patent/US10925167B2
folder image_downloads/US-10925167-B2 already exists, continuing to next publication_number
********************
i: 2335 / 37660 --- publication_number: US-10924410-B1
URL: https://patents.google.com/patent/US10924410B1
folder image_downloads/US-10924410-B1 already exists, continuing to next publication_number
********************
i: 2336

folder image_downloads/US-10860347-B1 already exists, continuing to next publication_number
********************
i: 3060 / 37660 --- publication_number: US-10863211-B1
URL: https://patents.google.com/patent/US10863211B1
folder image_downloads/US-10863211-B1 already exists, continuing to next publication_number
********************
i: 3061 / 37660 --- publication_number: US-10860190-B1
URL: https://patents.google.com/patent/US10860190B1
folder image_downloads/US-10860190-B1 already exists, continuing to next publication_number
********************
i: 3062 / 37660 --- publication_number: US-10860648-B1
URL: https://patents.google.com/patent/US10860648B1
folder image_downloads/US-10860648-B1 already exists, continuing to next publication_number
********************
i: 3063 / 37660 --- publication_number: US-D904458-S
URL: https://patents.google.com/patent/USD904458S1
folder image_downloads/US-D904458-S already exists, continuing to next publication_number
********************
i: 3064 / 37

...

downloading US10638645-20200428-D00004.png to image_downloads/US-10638645-B1/US10638645-20200428-D00004.png
downloading US10638645-20200428-D00005.png to image_downloads/US-10638645-B1/US10638645-20200428-D00005.png
downloading US10638645-20200428-D00006.png to image_downloads/US-10638645-B1/US10638645-20200428-D00006.png
downloading US10638645-20200428-D00007.png to image_downloads/US-10638645-B1/US10638645-20200428-D00007.png
downloading US10638645-20200428-D00008.png to image_downloads/US-10638645-B1/US10638645-20200428-D00008.png
https://patentimages.storage.googleapis.com/ea/43/8e/b5b20593c6a9a8/US10638645.pdf
downloading US10638645.pdf to image_downloads/US-10638645-B1/US10638645.pdf
********************
i: 5717 / 37660 --- publication_number: US-10638135-B1
URL: https://patents.google.com/patent/US10638135B1
making directory image_downloads/US-10638135-B1
found 12 images
found 1 PDFs
downloading US10638135-20200428-D00000.png to image_downloads/US-10638135-B1/US10638135-20200428

found 7 images
found 1 PDFs
downloading pct00001.png to image_downloads/KR-20200044088-A/pct00001.png
downloading pct00002.png to image_downloads/KR-20200044088-A/pct00002.png
downloading pct00003.png to image_downloads/KR-20200044088-A/pct00003.png
downloading pct00004.png to image_downloads/KR-20200044088-A/pct00004.png
downloading pct00005.png to image_downloads/KR-20200044088-A/pct00005.png
downloading pct00006.png to image_downloads/KR-20200044088-A/pct00006.png
downloading pct00007.png to image_downloads/KR-20200044088-A/pct00007.png
https://patentimages.storage.googleapis.com/a9/7a/5c/87b08fb544b299/KR20200044088A.pdf
downloading KR20200044088A.pdf to image_downloads/KR-20200044088-A/KR20200044088A.pdf
********************
i: 5723 / 37660 --- publication_number: CA-3003641-C
URL: https://patents.google.com/patent/CA3003641C
making directory image_downloads/CA-3003641-C
found 0 images
found 0 PDFs
********************
i: 5724 / 37660 --- publication_number: CN-111082489-A
URL: ht

downloading 2020064676-12.png to image_downloads/JP-2020064676-A/2020064676-12.png
https://patentimages.storage.googleapis.com/22/c3/44/8affc93538bb03/JP2020064676A.pdf
downloading JP2020064676A.pdf to image_downloads/JP-2020064676-A/JP2020064676A.pdf
********************
i: 5739 / 37660 --- publication_number: WO-2020078064-A1
URL: https://patents.google.com/patent/WO2020078064A1
making directory image_downloads/WO-2020078064-A1
found 6 images
found 1 PDFs
downloading PCTCN2019098089-appb-300001.png to image_downloads/WO-2020078064-A1/PCTCN2019098089-appb-300001.png
downloading PCTCN2019098089-appb-300002.png to image_downloads/WO-2020078064-A1/PCTCN2019098089-appb-300002.png
downloading PCTCN2019098089-appb-300003.png to image_downloads/WO-2020078064-A1/PCTCN2019098089-appb-300003.png
downloading PCTCN2019098089-appb-300004.png to image_downloads/WO-2020078064-A1/PCTCN2019098089-appb-300004.png
downloading PCTCN2019098089-appb-300005.png to image_downloads/WO-2020078064-A1/PCTCN20190

found 0 images
found 0 PDFs
********************
i: 5750 / 37660 --- publication_number: EP-3639156-A1
URL: https://patents.google.com/patent/EP3639156A1
making directory image_downloads/EP-3639156-A1
found 0 images
found 0 PDFs
********************
i: 5751 / 37660 --- publication_number: US-10628790-B1
URL: https://patents.google.com/patent/US10628790B1
making directory image_downloads/US-10628790-B1
found 10 images
found 1 PDFs
downloading US10628790-20200421-D00000.png to image_downloads/US-10628790-B1/US10628790-20200421-D00000.png
downloading US10628790-20200421-D00001.png to image_downloads/US-10628790-B1/US10628790-20200421-D00001.png
downloading US10628790-20200421-D00002.png to image_downloads/US-10628790-B1/US10628790-20200421-D00002.png
downloading US10628790-20200421-D00003.png to image_downloads/US-10628790-B1/US10628790-20200421-D00003.png
downloading US10628790-20200421-D00004.png to image_downloads/US-10628790-B1/US10628790-20200421-D00004.png
downloading US10628790-202

KeyboardInterrupt: 